In [ ]:
!pip install --upgrade setuptools
!pip install pystan==2.19.1.1
!pip install fbprophet

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 7.6 MB/s eta 0:00:00
  Attempting uninstall: setuptools
    Found existing installation: setuptools 67.6.0
    Uninstalling setuptools-67.6.0:
      Successfully uninstalled setuptools-67.6.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
ipython 7.9.0 requires jedi>=0.10, which is not installed.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.2/16.2 MB 21.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pystan: filename=pystan-2.19.1.1-cp39-cp39-linux_x86_64.whl size=61826397 sha256=d79afdffb0ff7e46f037af0f99bfffe597ab36ddb19801300843b316d5b092e2
  Stored in directory: /root/.c

In [ ]:
import pandas as pd
import numpy as np
import os
import re
from fbprophet import Prophet
from fbprophet.plot import plot_plotly, plot_components_plotly
import plotly
import plotly.graph_objs as go
import holidays
from sklearn.metrics import mean_absolute_error, mean_squared_error
import seaborn as sns
import matplotlib.pyplot as plt
from fbprophet.diagnostics import cross_validation, performance_metrics
import itertools

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
cd = pd.read_parquet('/content/drive/MyDrive/MGT6748_Steelcase/final_clean_data_0317.parquet')

In [ ]:
us_holidays = holidays.UnitedStates()

start_date = pd.to_datetime('2022-09-01')
end_date = pd.to_datetime('2023-12-31')

holidays_df = pd.DataFrame({
    'holiday': 'US Holidays',
    'ds': pd.to_datetime([d for d in us_holidays[start_date:end_date]]),
    'lower_window': 0,
    'upper_window': 0,
})
# Add weekends
weekends_df = pd.DataFrame({
    'holiday': 'weekend',
    'ds': pd.date_range(start_date, end_date, freq='W-SAT').append(pd.date_range(start_date, end_date, freq='W-SUN')),
    'lower_window': 0,
    'upper_window': 0,
})

# Concatenate holidays and weekends
holidays_and_weekends_df = pd.concat([holidays_df, weekends_df])

In [ ]:
rdc_list = ['CC','EP', 'GM', 'NG', 'NT', 'WW']
# 'CC','EP', 'GM', 'NC', 'NG', 'NT', 'WW'
col_nm = ['total_inv',	'inc_inv',	'out_inv',	'vol_total']

In [ ]:
def create_pred_df(df, rdc, col_name,rmse_val):
    # create new dataframe with dates
    pred_df = pd.DataFrame({'date': df['ds']})
    
    # add predicted values to dataframe
    pred_df['building'] = rdc
    pred_df['predicted_value'] = df['yhat']
    pred_df['rmse'] = rmse_val
    pred_df['predicted_name'] = col_name
    
    # filter forecast for certain dates
    pred_dates = pd.date_range(start='2023-01-01', end='2023-04-30', freq='D')
    pred_df_new = pred_df.loc[pred_df['date'].isin(pred_dates)]
    
    return pred_df_new

In [ ]:
def find_best_model(df):
    param_grid = {  
        'changepoint_prior_scale': [ 0.01, 0.1, 0.5],
        'seasonality_prior_scale': [0.01, 0.1, 1.0],
        'n_changepoints': [25, 50],
        'seasonality_mode': ['additive', 'multiplicative'],
    }

    # Generate all combinations of parameters
    all_params = [dict(zip(param_grid.keys(), v)) for v in itertools.product(*param_grid.values())]
    rmses = []  # Store the RMSEs for each params here

    # Use cross validation to evaluate all parameters
    for params in all_params:
        m = Prophet(**params).fit(df)  # Fit model with given params
        df_cv = cross_validation(model=m, initial='80 days', period='30 days', horizon='7 days')
        df_p = performance_metrics(df_cv, rolling_window=1)
        rmses.append(df_p['rmse'].values[0])

    # Find the best parameters
    tuning_results = pd.DataFrame(all_params)
    tuning_results['rmse'] = rmses

    best_params = all_params[np.argmin(rmses)]
    m = Prophet(holidays=holidays_and_weekends_df, 
                changepoint_prior_scale=best_params['changepoint_prior_scale'], 
                seasonality_prior_scale=best_params['seasonality_prior_scale'], 
                n_changepoints=best_params['n_changepoints'], 
                seasonality_mode=best_params['seasonality_mode'])
    
    rmse_val = rmses[np.argmin(rmses)]

    return m, rmse_val


In [ ]:
def run_prophet(cd):
    pred_df_new = pd.DataFrame()

    for rdc in rdc_list:
        cd1 = cd.loc[(cd['Location'] == "In Building") & (cd['rdc'] == rdc) & (cd['report_date'] >= '2022-09-15') & (cd['report_date'] <= '2022-12-15')]
        cd2 = cd1.groupby(['report_date']).agg(total_inv=('total', 'sum'), inc_inv=('inc', 'sum'),out_inv=('out', 'sum'), vol_total=('total_vol', 'sum')).reset_index()

        for col_name in col_nm:
          # Load the data - date and y variable
          df_pro=cd2[["report_date",col_name]]

          # Rename the columns
          df_pro.columns = ['ds','y']

          # Convert to datetime
          df_pro['ds'] = pd.to_datetime(df_pro['ds'])

          m, rmse_val = find_best_model(df_pro)
          m.fit(df_pro)
          future = m.make_future_dataframe(periods=120) 
          forecast = m.predict(future)

          forecast_filtered = forecast[~forecast['ds'].isin(holidays_and_weekends_df['ds'])]

          new_data = create_pred_df(forecast_filtered, rdc, col_name, rmse_val)
          pred_df_new = pd.concat([pred_df_new, new_data], ignore_index=True)
        
    return pred_df_new

In [ ]:
df_frsct = run_prophet(cd)
df_frsct.to_csv('/content/drive/MyDrive/MGT6748_Steelcase/frsct_w_tuning.csv', index=False) 

<ipython-input-59-3b64b7197c4f>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_pro['ds'] = pd.to_datetime(df_pro['ds'])
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
INFO:fbprophet:Making 1 forecasts with cutoffs between 2022-12-08 00:00:00 and 2022-12-08 00:00:00


  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py

  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py

...

/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py

  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
INFO:fbprophet:n_changepoints greater than number of observations. Using 44.
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to 

  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
INFO:fbprophet:n_changepoints greater than number of observations. Using 44.
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
/usr/local/lib/python3.9/dist-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  components = components.append(new_comp)
INFO:fbprophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.
INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to 